In [5]:
# wsi处理 
step1 = False
step2 = False
step3 = True
## step1 清理低质量图
import openslide 
import os 
import shutil
import pandas as pd

path = r'/home/sci/Disk2/tcga_crc/DATA_DIRECTORY'
trash_path = r'/home/sci/Disk2/tcga_crc/trash'
slides = os.listdir(path)
slides = [slide for slide in slides if os.path.isfile(os.path.join(path,slide))]
# print(slides)
i = 0
if step1:
    for slide in slides:
        slide_path = os.path.join(path,slide)
        slide_object = openslide.OpenSlide(slide_path)
        if slide_object.level_count == 2:
            shutil.move(slide_path,trash_path)
            i += 1
            print(f'already process {i} slides to trash')

## step 2 20/40 划分
if step2:
    for slide in slides:
        slide_path = os.path.join(path,slide)
        slide_object = openslide.OpenSlide(slide_path)
        if slide_object.properties['aperio.AppMag'] == '40':
            shutil.move(slide_path, os.path.join(path,'40'))
        else:
            shutil.move(slide_path, os.path.join(path,'20'))
        i += 1
        print(f'already process {i} slides to magfilefolder')
## 删除不能用的WSI
if step3:
    
    data_dir = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC/WSI'
    # trash_20 = r'/home/sci/Disk2/tcga_crc/trash/trash_20'
    # os.makedirs(trash_20,exist_ok=True)
    all_slides = os.listdir(data_dir)
    patch_dir = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC/BLOCKS_level-1/patches'
    feat_dir = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC/FEATURES_levle-1/pt_files'
    all_patches = os.listdir(patch_dir)
    for slide in all_slides:
        slide_name,_ = os.path.splitext(slide)
        slide_path = os.path.join(data_dir,slide)
        # patch_path = os.path.join(patch_5_dir,f'{slide_name}.h5')
        if not os.path.exists(os.path.join(patch_dir,f'{slide_name}.h5')):
            shutil.move(slide_path, '/home/sci/Disk_data/Datasets/error')
            os.remove(f'/home/sci/Disk_data/Datasets/TCGA-NSCLC/BLOCKS_level-1/masks/{slide_name}.jpg')
            # os.remove(f'/home/sci/Disk_data/Datasets/TCGA-NSCLC/BLOCKS/thumbnails/{slide_name}_thumb.jpg')


In [1]:
## csv_file process
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'
import pandas as pd
import os

df_csv = pd.read_csv('dataset_csv/TCGA-NSCLC.csv')
dataset_dir = '/home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/WSI'
index = df_csv.index
rows_to_delete = []
for name in os.listdir(dataset_dir):
    slide_id = os.path.splitext(name)[0]

    row_index = df_csv[df_csv['slide_id'] == slide_id].index
    rows_to_delete.append(row_index.item())
    
remaining_index = index.difference(rows_to_delete)
df_delete = df_csv.drop(remaining_index).reset_index(drop=True)
df_delete
# df = df_csv.drop(~rows_to_delete)

df_delete.to_csv('dataset_csv/tcga_lung_subtyping_sub.csv')

In [ ]:
# WSI 属性查看
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

import openslide
import os
import torch
slide_path = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC/WSI/TCGA-05-4244-01A-01-BS1.svs'
path = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/WSI'
# # ---->> for single slide
# slide = openslide.OpenSlide(slide_path)
# slide.dimensions
# slide.associated_images
# slide.level_dimensions
# slide.level_count
# slide.properties['aperio.AppMag']
# slide.properties['aperio.MPP']

# ---->> for slide folder
slides = os.listdir(path)
dimentions_list = []
for slide in slides:
    slide = os.path.join(path,slide)
    slide = openslide.OpenSlide(slide)
    print(slide.level_dimensions)
    print(slide.properties['aperio.AppMag'])
    print(slide.level_count)
    # slide = slide.get_thumbnail((slide.level_dimensions[-1]))
    # slide.save(r'/home/sci/Disk2/tcga_crc/DATA_DIRECTORY/test')
    # print('save_success')
    # dimentions_list.append(slide.level_dimensions[-1])
# dimentions_list=torch.tensor(dimentions_list)
# index = torch.topk(dimentions_list, 1, dim=1)
# maxMap = torch.index_select(dimentions_list, index=index, dim=0 )
# maxMap




In [ ]:
# ----> wsi transfer
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

import openslide
import os
import torch
import glob
import shutil

path = r"/home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/WSI"
path_20 = os.path.join(path, '20')
path_40 = os.path.join(path, '40')
os.makedirs(path_20, exist_ok=True)
os.makedirs(path_40, exist_ok=True)
slide_list = glob.glob(os.path.join(path, '*.svs'))

# for slide_path in slide_list:
#     # slide_path = os.path.join(path, slide)
#     slide_obj = openslide.open_slide(slide_path)

#     if slide_obj.level_count == 3:
#         shutil.move(slide_path, path_20)
#     elif slide_obj.level_count == 4:
#         shutil.move(slide_path, path_40)

# ----> trans back
allslide_path = glob.glob(os.path.join(path, '*/*.svs'))
for slide_path in allslide_path:
    shutil.move(slide_path, path)



In [12]:
import h5py
path = r'E:\Workspace\Project\CLAM\data\RESULTS_DIRECTORY\patches\TCGA-A6-2671-01A-01-BS1.h5'
f = h5py.File(path,'r')
f.keys()
data = f.get('coords')
print(data)
data.shape


<HDF5 dataset "coords": shape (2989, 2), type "<i4">


(2989, 2)

## Step_1 get patch

source svs 文件地址\
save_dir 结果文件\

In [ ]:
'''
python create_patches_fp.py \
--source 'svs_dir' \
--save_dir 'result_dir' \
--patch_size 256 \
--seg \ # 分割=True
--patch \ # 切分patch=True
--stitch \ # 
process_list_autogen.csv # 这里记录了每张 image 的处理的参数
'''


In [5]:
##改 savedir and patch_level
!python create_patches_fp.py --source /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/WSI/20 --save_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1 --patch_level 0 --patch_size 256 --seg --patch --stitch

source:  /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/WSI/20
patch_save_dir:  /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/patches
mask_save_dir:  /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/masks
stitch_save_dir:  /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/stitches
thumbnail_save_dir:  /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/thumbnails
source : /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/WSI/20
save_dir : /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1
patch_save_dir : /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/patches
mask_save_dir : /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/masks
stitch_save_dir : /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/stitches
thumbnail_save_dir : /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/thumbnails
{'seg_params': {'seg_level': -1, 'sthresh': 8, 'mthresh': 7, 'close': 4, 'use_otsu': False, 'keep_ids': 'none', 'exclude_ids': 'none'},

## Step_2 get patch features
data_h5_dir  输出文件地址\
data_slide_dir svs文件地址\
上一步生成的csv csv_path\
feat_dir 输出文件地址\


In [ ]:
'''
CUDA_VISIBLE_DEVICES=0 python extract_features_fp.py \
--data_h5_dir data/RESULTS_DIRECTORY/patches \
--data_slide_dir /media/yuansh/14THHD/CLAM/DataSet/toy_example \
--csv_path /media/yuansh/14THHD/CLAM/Step_2.csv \
--feat_dir /media/yuansh/14THHD/CLAM/FEATURES_DIRECTORY \
--batch_size 512 \
--slide_ext .svs
'''
!python extract_features_fp.py\
    --data_h5_dir E:\Workspace\Project\CLAM\data\RESULTS_DIRECTORY \
    --data_slide_dir F:/Download/TCGA \
    --csv_path data\RESULTS_DIRECTORY\Step_2.csv \
    --feat_dir E:\Workspace\Project\CLAM\data\FEATURES_DIRECTORY \
    --batch_size 256 \
    --slide_ext .svs


In [8]:
# 生成第2步骤需要的csv文件
from utils.csv_gen import *

csv_dir = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/process_list_autogen.csv'
# sort_csv = pd.read_csv(csv_dir).sort_values('slide_id')
result_dir = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/step2_get_features.csv'
patch_dir = r'/home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/patches'
csv_gen_step1(csv_dir,result_dir,patch_dir)

In [11]:
!CUDA_VISIBLE_DEVICES=0 python extract_features_fp.py --data_h5_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1 \
--data_slide_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/WSI \
--csv_path /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/step2_get_features.csv \
--feat_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/FEATURES_level1 --batch_size 512 --slide_ext .svs

initializing dataset
loading model checkpoint

progress: 0/828
TCGA-18-3406-01Z-00-DX1
downsample [4.00003118 4.00004558]
downsampled_level_dim [32068 21941]
level_dim [32068 21941]
name TCGA-18-3406-01Z-00-DX1
patch_level 1
patch_size 256
save_path /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/patches

feature extraction settings
target patch size:  None
pretrained:  True
transformations:  Compose(
    ToTensor()
    Normalize(mean=(0.485, 0.456, 0.406), std=(0.229, 0.224, 0.225))
)
processing /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/BLOCKS_level1/patches/TCGA-18-3406-01Z-00-DX1.h5: total of 13 batches
batch 0/13, 0 files processed

computing features for /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/FEATURES_level1/h5_files/TCGA-18-3406-01Z-00-DX1.h5 took 20.450263023376465 s
features size:  (6431, 1024)
coordinates size:  (6431, 2)

progress: 1/828
TCGA-18-3407-01Z-00-DX1
downsample [4.00003425 4.        ]
downsampled_level_dim [29196 20020]
level_dim [29196 20020]
name

## step3 Create split
注意修改Create_split_seq.py文件中的csv路径

In [ ]:
from utils.csv_gen import * 
path = r'/home/sci/Disk_data/TCGA-NSCLC/WSI'
# sort_csv = pd.read_csv(csv_dir).sort_values('slide_id')
result_dir = r'/home/sci/Disk_data/TCGA-NSCLC/RESULTS_DIRECTORY/step3_get_splits.csv' ## 5 + 20
patch_dir = r'/home/sci/Disk_data/TCGA-NSCLC/RESULTS_DIRECTORY/patches'
csv_gen_test(path,result_dir)

In [9]:
!python create_splits_seq.py --task task_2_tumor_subtyping --seed 1 --label_frac 1 --k 5 --csv_path dataset_csv/tcga_lung_subtyping_sub.csv

/home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/datasets/dataset_generic.py:104: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True or False to avoid this warning.
  label = stats.mode(label)[0]
/home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/datasets/dataset_generic.py:104: FutureWarning: Unlike other reduction functions (e.g. `skew`, `kurtosis`), the default behavior of `mode` typically preserves the axis it acts along. In SciPy 1.11.0, this behavior will change: the default value of `keepdims` will become False, the `axis` over which the statistic is taken will be eliminated, and the value None will no longer be accepted. Set `keepdims` to True o

## Step4 Train
注意修改main.py中的csv路径

CUDA_VISIBLE_DEVICES=0 python main.py \
--drop_out \
--early_stopping \
--lr 2e-4 \
--k 10 \
--label_frac 0.75 \
--exp_code task_1_tumor_vs_normal_CLAM_50 --weighted_sample --bag_loss ce --inst_loss svm --task task_1_tumor_vs_normal --model_type clam_sb --log_data \
--data_root_dir /media/yuansh/14THHD/CLAM/FEATURES_DIRECTORY



In [4]:
!CUDA_VISIBLE_DEVICES=0 python main.py --drop_out --early_stopping --lr 2e-4 --k 5 --label_frac 1\
--exp_code tcga_nsclc_sub_100_level3_mb --weighted_sample --bag_loss ce --inst_loss svm \
--task task_2_tumor_subtyping --model_type clam_mb --log_data --data_root_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/FEATURES_level3 \
--split_dir /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100 --subtyping \
--csv_path dataset_csv/tcga_lung_subtyping_sub.csv


Load Dataset
label column: label
label dictionary: {'LUAD': 0, 'LUSC': 1}
number of classes: 2
slide-level counts:  
 0    394
1    434
Name: label, dtype: int64
Patient-LVL; Number of samples registered in class 0: 333
Slide-LVL; Number of samples registered in class 0: 394
Patient-LVL; Number of samples registered in class 1: 400
Slide-LVL; Number of samples registered in class 1: 434
split_dir:  /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100
################# Settings ###################
num_splits:  5
k_start:  -1
k_end:  -1
task:  task_2_tumor_subtyping
max_epochs:  200
results_dir:  ./results
lr:  0.0002
experiment:  tcga_nsclc_sub_100_level3_mb
reg:  1e-05
label_frac:  1.0
bag_loss:  ce
seed:  1
model_type:  clam_mb
model_size:  small
use_drop_out:  True
weighted_sample:  True
opt:  adam
bag_weight:  0.7
inst_loss:  svm
B:  8
split_dir:  /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100

Training Fold 0!

Init train/val/t

In [33]:
!CUDA_VISIBLE_DEVICES=0 python main.py --drop_out --early_stopping --lr 2e-4 --k 5 --label_frac 0.75 \
--exp_code tcga_nsclc_75_level1_transmil --weighted_sample --bag_loss ce --inst_loss svm \
--task task_2_tumor_subtyping --model_type transmil --log_data --data_root_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC/FEATURES_level1 \
--split_dir /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/task_2_tcga_subtyping_75 --subtyping


Load Dataset
label column: label
label dictionary: {'Normal': 0, 'LUAD': 1, 'LUSC': 2}
number of classes: 3
slide-level counts:  
 1    1185
0     524
2    1140
Name: label, dtype: int64
Patient-LVL; Number of samples registered in class 0: 3
Slide-LVL; Number of samples registered in class 0: 524
Patient-LVL; Number of samples registered in class 1: 517
Slide-LVL; Number of samples registered in class 1: 1185
Patient-LVL; Number of samples registered in class 2: 500
Slide-LVL; Number of samples registered in class 2: 1140
split_dir:  /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/task_2_tcga_subtyping_75
################# Settings ###################
num_splits:  5
k_start:  -1
k_end:  -1
task:  task_2_tumor_subtyping
max_epochs:  200
results_dir:  ./results
lr:  0.0002
experiment:  tcga_nsclc_75_level1_transmil
reg:  1e-05
label_frac:  0.75
bag_loss:  ce
seed:  1
model_type:  transmil
model_size:  small
use_drop_out:  True
weighted_sample:  True
opt:  adam
bag_weight:

### TransformerMIL实验结果

In [2]:
!CUDA_VISIBLE_DEVICES=0 python main.py --drop_out --early_stopping --lr 2e-4 --k 5 --label_frac 1 \
--exp_code tcga_nsclc_sub_100_level3_transmil --weighted_sample --bag_loss ce --inst_loss svm \
--task task_2_tumor_subtyping --model_type transmil --log_data --data_root_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/FEATURES_level3 \
--split_dir /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100 --subtyping \
--csv_path dataset_csv/tcga_lung_subtyping_sub.csv

^C
Traceback (most recent call last):
  File "/home/sci/PycharmProjects/chaofan/projects/CLAM/main.py", line 11, in <module>
    from utils.core_utils import train
  File "/home/sci/PycharmProjects/chaofan/projects/CLAM/utils/core_utils.py", line 6, in <module>
    from datasets.dataset_generic import save_splits
  File "/home/sci/PycharmProjects/chaofan/projects/CLAM/datasets/dataset_generic.py", line 5, in <module>
    import pandas as pd
  File "/home/sci/anaconda3/envs/lcf/lib/python3.9/site-packages/pandas/__init__.py", line 48, in <module>
    from pandas.core.api import (
  File "/home/sci/anaconda3/envs/lcf/lib/python3.9/site-packages/pandas/core/api.py", line 47, in <module>
    from pandas.core.groupby import (
  File "/home/sci/anaconda3/envs/lcf/lib/python3.9/site-packages/pandas/core/groupby/__init__.py", line 1, in <module>
    from pandas.core.groupby.generic import (
  File "/home/sci/anaconda3/envs/lcf/lib/python3.9/site-packages/pandas/core/groupby/generic.py", line 7

In [1]:
!CUDA_VISIBLE_DEVICES=0 python main.py --drop_out --early_stopping --lr 2e-4 --k 5 --label_frac 1 \
--exp_code tcga_nsclc_sub_100_level1_transmil --weighted_sample --bag_loss ce --inst_loss svm \
--task task_2_tumor_subtyping --model_type transmil --log_data --data_root_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/FEATURES_level1 \
--split_dir /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100 --subtyping \
--csv_path dataset_csv/tcga_lung_subtyping_sub.csv


Load Dataset
label column: label
label dictionary: {'LUAD': 0, 'LUSC': 1}
number of classes: 2
slide-level counts:  
 0    394
1    434
Name: label, dtype: int64
Patient-LVL; Number of samples registered in class 0: 333
Slide-LVL; Number of samples registered in class 0: 394
Patient-LVL; Number of samples registered in class 1: 400
Slide-LVL; Number of samples registered in class 1: 434
split_dir:  /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100
################# Settings ###################
num_splits:  5
k_start:  -1
k_end:  -1
task:  task_2_tumor_subtyping
max_epochs:  200
results_dir:  ./results
lr:  0.0002
experiment:  tcga_nsclc_sub_100_level1_transmil
reg:  1e-05
label_frac:  1.0
bag_loss:  ce
seed:  1
model_type:  transmil
model_size:  small
use_drop_out:  True
weighted_sample:  True
opt:  adam
bag_weight:  0.7
inst_loss:  svm
B:  8
split_dir:  /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100

Training Fold 0!

Init trai

### proposed

In [ ]:
!CUDA_VISIBLE_DEVICES=0 python main_myself.py --drop_out --early_stopping --lr 2e-4 --max_lr 2e-3 --k 5 --label_frac 1 --opt Radam\
--exp_code tcga_nsclc_sub_100_level13_mcbat_sb_depth3_wormup5-25Radam_FLASH --weighted_sample --bag_loss ce --inst_loss svm \
--task task_2_tumor_subtyping --model_type mcbat_sb --log_data --data_low_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/FEATURES_level3 \
--data_high_dir /home/sci/Disk_data/Datasets/TCGA-NSCLC-sub/FEATURES_level1 \
--split_dir /home/sci/Disk_data/SCI_Projects/chaofan/projects/CLAM/splits/tcga_nsclc_100 --subtyping \
--csv_path dataset_csv/tcga_lung_subtyping_sub.csv

## eval

CUDA_VISIBLE_DEVICES=0 python eval.py \
--drop_out \
--k 10 \
--models_exp_code task_1_tumor_vs_normal_CLAM_50_s1 \
--save_exp_code task_1_tumor_vs_normal_CLAM_50_s1_cv \
--task task_1_tumor_vs_normal \
--model_type clam_sb \
--results_dir results \
--data_root_dir /media/yuansh/14THHD/CLAM/FEATURES_DIRECTORY


In [24]:
!python eval.py --drop_out --k 5 --models_exp_code tcga_crc_5_s1 \
    --save_exp_code tcga_crc_5_cv \
    --task task_1_tumor_vs_normal --model_type clam_sb --results_dir results \
    --data_root_dir /home/sci/Disk2/tcga_crc/FEATURES_DIRECTORY_5

{'task': 'task_1_tumor_vs_normal', 'split': 'test', 'save_dir': './eval_results/EVAL_tcga_crc_5_cv', 'models_dir': 'results/tcga_crc_5_s1', 'model_type': 'clam_sb', 'drop_out': True, 'model_size': 'small'}
label column: label
label dictionary: {'normal_tissue': 0, 'tumor_tissue': 1}
number of classes: 2
slide-level counts:  
 1    1342
0      91
Name: label, dtype: int64
Patient-LVL; Number of samples registered in class 0: 3
Slide-LVL; Number of samples registered in class 0: 91
Patient-LVL; Number of samples registered in class 1: 497
Slide-LVL; Number of samples registered in class 1: 1342
Init Model
CLAM_SB(
  (attention_net): Sequential(
    (0): Linear(in_features=1024, out_features=512, bias=True)
    (1): ReLU()
    (2): Dropout(p=0.25, inplace=False)
    (3): Attn_Net_Gated(
      (attention_a): Sequential(
        (0): Linear(in_features=512, out_features=256, bias=True)
        (1): Tanh()
        (2): Dropout(p=0.25, inplace=False)
      )
      (attention_b): Sequential(
 

In [1]:
!python create_heatmaps.py --config config_template.yaml


exp_arguments
n_classes : 2
save_exp_code : HEATMAP_OUTPUT
raw_save_dir : heatmaps/heatmap_raw_results
production_save_dir : heatmaps/heatmap_production_results
batch_size : 384

data_arguments
data_dir : heatmaps/demo/slides/
data_dir_key : source
process_list : myself.csv
preset : presets/bwh_brca.csv
slide_ext : .svs
label_dict : {'tumor': 1, 'normal': 0}

patching_arguments
patch_size : 256
overlap : 0.5
patch_level : 0
custom_downsample : 1

model_arguments
ckpt_path : heatmaps/demo/ckpts/s_4_checkpoint.pt
model_type : clam_sb
initiate_fn : initiate_model
model_size : small
drop_out : True

heatmap_arguments
vis_level : 1
alpha : 0.4
blank_canvas : False
save_orig : True
save_ext : jpg
use_ref_scores : True
blur : False
use_center_shift : True
use_roi : False
calc_heatmap : True
binarize : False
binary_thresh : -1
custom_downsample : 1
cmap : jet

sample_arguments
samples : [{'name': 'topk_high_attention', 'sample': True, 'seed': 1, 'k': 15, 'mode': 'topk'}]
Continue? Y/N ^C
Trac